In [1]:
from pulp import *
import numpy as np
import pandas as pd
import random
import json
import pdb

In [2]:
# Inputs

no_of_customers = 40 # Total number of customers
no_of_depots = 4 # Total number of depots
total_vehicles = 16 # Total number of vehicles
trips_per_vehicle = 3 # Maximum number of trips per vehicle

D_V = {40:[0,1,2,3], 41:[4,5,6,7], 42:[8,9,10,11], 43:[12,13,14,15]} # Depot to vehicle mapping

time_window = [60,240] # Time window at which customers are served
H = 300 # Time horizon
s = 5 # service time at customer
service_at_depot = 5 # service time at depot

In [3]:
k = []
veh_start_point = []

for i, j in D_V.items():
    k += j
    veh_start_point.append(i)

print(k)
print(veh_start_point)

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15]
[40, 41, 42, 43]


In [4]:
# Pickup for customers

p = [random.randint(3,6) for _ in range(no_of_customers)]
temp = [0] * no_of_depots
p.extend(temp)
print(p)

[3, 6, 6, 4, 4, 5, 6, 4, 6, 5, 4, 5, 4, 6, 4, 4, 3, 3, 4, 5, 3, 5, 6, 6, 5, 4, 6, 5, 4, 5, 5, 5, 6, 3, 3, 3, 5, 3, 3, 6, 0, 0, 0, 0]


In [5]:
# Pickup for customers

with open('p.json', 'w') as f:
    json.dump(p, f)

In [6]:
# Delivery for customers

q = [random.randint(5,10) for _ in range(no_of_customers)]
temp = [0] * no_of_depots
q.extend(temp)
print(q)

[9, 7, 6, 8, 5, 5, 10, 6, 6, 5, 5, 9, 10, 6, 7, 5, 7, 8, 9, 6, 10, 7, 5, 8, 5, 9, 6, 5, 9, 8, 10, 6, 5, 7, 6, 10, 5, 7, 6, 7, 0, 0, 0, 0]


In [7]:
with open('q.json', 'w') as f:
    json.dump(q, f)

In [8]:
C = list(range(no_of_customers))
D = list(range(len(C), len(C) + no_of_depots, 1))
W = list(range(trips_per_vehicle))
Q = 25

In [9]:
print(W)

[0, 1, 2]


In [10]:
print(C)
print(D)

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39]
[40, 41, 42, 43]


In [11]:
import random

def generate_random_coordinates(num_points, x_range=(0, 25), y_range=(0, 25)):
    return [(random.randint(x_range[0], x_range[1]),
             random.randint(y_range[0], y_range[1])) for _ in range(num_points)]

# Define the number of customers and depots
num_customers = no_of_customers
num_depots = no_of_depots

# Generate random coordinates for customers and depots
customer_coordinates = generate_random_coordinates(num_customers)
depot_coordinates = generate_random_coordinates(num_depots)

# Create dictionaries for customers and depots with their coordinates
customers_coord = {f'Cust_{i+1}': coord for i, coord in enumerate(customer_coordinates)}
depots = {f'Depot_{i+1}': coord for i, coord in enumerate(depot_coordinates)}

# Print the dictionaries
print("Customers:")
print(customers_coord)

print("\nDepots:")
print(depots)

Customers:
{'Cust_1': (21, 19), 'Cust_2': (10, 9), 'Cust_3': (0, 14), 'Cust_4': (11, 8), 'Cust_5': (10, 12), 'Cust_6': (7, 13), 'Cust_7': (20, 5), 'Cust_8': (9, 17), 'Cust_9': (15, 16), 'Cust_10': (23, 11), 'Cust_11': (25, 25), 'Cust_12': (14, 21), 'Cust_13': (24, 6), 'Cust_14': (6, 5), 'Cust_15': (10, 7), 'Cust_16': (18, 14), 'Cust_17': (12, 15), 'Cust_18': (13, 2), 'Cust_19': (5, 22), 'Cust_20': (13, 3), 'Cust_21': (4, 24), 'Cust_22': (5, 13), 'Cust_23': (16, 6), 'Cust_24': (6, 21), 'Cust_25': (25, 12), 'Cust_26': (9, 14), 'Cust_27': (18, 5), 'Cust_28': (6, 4), 'Cust_29': (18, 6), 'Cust_30': (4, 5), 'Cust_31': (12, 6), 'Cust_32': (17, 3), 'Cust_33': (1, 9), 'Cust_34': (7, 10), 'Cust_35': (11, 15), 'Cust_36': (11, 3), 'Cust_37': (19, 23), 'Cust_38': (19, 10), 'Cust_39': (6, 0), 'Cust_40': (6, 15)}

Depots:
{'Depot_1': (4, 25), 'Depot_2': (11, 11), 'Depot_3': (1, 19), 'Depot_4': (20, 9)}


In [12]:
# Store the dictionary as JSON

with open('customers.json', 'w') as json_file:
    json.dump(customers_coord, json_file)
    
with open('depots.json', 'w') as json_file:
    json.dump(depots, json_file)

In [13]:
# Function to calculate Manhattan distance (travel time) between two coordinates
def calculate_manhattan_distance(coord1, coord2):
    x1, y1 = coord1
    x2, y2 = coord2
    return abs(x2 - x1) + abs(y2 - y1)

# Function to generate random time windows for customers
def generate_random_time_windows(num_customers, min_earliest_time, max_latest_time):
    return [(random.randint(min_earliest_time, max_latest_time),
             random.randint(min_earliest_time, max_latest_time))
            for _ in range(num_customers)]

# Define the time window range (in minutes)
min_earliest_time = time_window[0]
max_latest_time = time_window[1]

# Create a 2D array to store travel times
num_customers = len(customers_coord)
num_depots = len(depots)
num_locations = num_customers + num_depots

# Assign sequential numbers to customers and depots
customer_numbers = {customer: i + 1 for i, customer in enumerate(customers_coord.keys())}
depot_numbers = {depot: num_customers + i + 1 for i, depot in enumerate(depots.keys())}
all_locations = {**customer_numbers, **depot_numbers}

d = np.zeros((num_locations, num_locations), dtype=int)

# Generate random time windows for customers
customer_time_windows = generate_random_time_windows(num_customers, min_earliest_time, max_latest_time)
customer_time_windows = [(min(e, l), max(e, l)) for e, l in customer_time_windows]

# Calculate travel time between customers and depots
for i, location_i in enumerate(all_locations):
    for j, location_j in enumerate(all_locations):
        coord_i = customers_coord[location_i] if location_i in customers_coord else depots[location_i]
        coord_j = customers_coord[location_j] if location_j in customers_coord else depots[location_j]
        d[i, j] = calculate_manhattan_distance(coord_i, coord_j)
        
print(d)
print(customer_time_windows)

[[ 0 21 26 ... 18 20 11]
 [21  0 15 ...  3 19 10]
 [26 15  0 ... 14  6 25]
 ...
 [18  3 14 ...  0 18 11]
 [20 19  6 ... 18  0 29]
 [11 10 25 ... 11 29  0]]
[(160, 200), (149, 189), (77, 101), (82, 197), (89, 94), (80, 107), (109, 109), (110, 229), (82, 85), (99, 111), (158, 222), (145, 215), (125, 191), (97, 193), (184, 235), (133, 189), (61, 231), (90, 141), (77, 150), (133, 162), (152, 213), (67, 193), (128, 155), (183, 197), (128, 149), (158, 159), (90, 231), (74, 201), (113, 135), (121, 190), (137, 212), (135, 169), (69, 75), (111, 113), (153, 190), (205, 221), (117, 118), (132, 183), (72, 95), (64, 228)]


In [14]:
# Convert the matrix to a nested list for JSON serialization
d = d.tolist()

# Store the matrix as JSON
with open('d.json', 'w') as json_file:
    json.dump(d, json_file)

In [15]:
i = 0
j = 1
ear = []
lat = []

for k in customer_time_windows:
    ear.append(k[i])
    lat.append(k[j])
    
print(ear)
print(lat)

[160, 149, 77, 82, 89, 80, 109, 110, 82, 99, 158, 145, 125, 97, 184, 133, 61, 90, 77, 133, 152, 67, 128, 183, 128, 158, 90, 74, 113, 121, 137, 135, 69, 111, 153, 205, 117, 132, 72, 64]
[200, 189, 101, 197, 94, 107, 109, 229, 85, 111, 222, 215, 191, 193, 235, 189, 231, 141, 150, 162, 213, 193, 155, 197, 149, 159, 231, 201, 135, 190, 212, 169, 75, 113, 190, 221, 118, 183, 95, 228]


In [16]:
with open('ear.json', 'w') as f:
    json.dump(ear, f)
    
with open('lat.json', 'w') as f:
    json.dump(lat, f)

In [17]:
# Setting up the problem:

prob = LpProblem("Distance_minimization", LpMinimize)

# Decision variables:

a = LpVariable.dicts("Allocation", [(i,j) for i in C for j in D], lowBound=0, cat='Binary')

In [18]:
# Objective function:

prob += lpSum(a[(i,j)] * d[i][j] for i in C for j in D)

In [19]:
# Constraint:

# 1) Each customer should be allocated to only one depot:

for i in C:
    prob += lpSum((a[(i,j)]) for j in D) == 1

In [20]:
prob.solve()

1

In [21]:
print("Status", LpStatus[prob.status])

Status Optimal


In [22]:
print("Total distance = ", value(prob.objective))

Total distance =  306.0


In [23]:
for v in prob.variables():
    if v.varValue > 0:
        print(v.name, "=", v.varValue)

Allocation_(0,_43) = 1.0
Allocation_(1,_41) = 1.0
Allocation_(10,_43) = 1.0
Allocation_(11,_41) = 1.0
Allocation_(12,_43) = 1.0
Allocation_(13,_41) = 1.0
Allocation_(14,_41) = 1.0
Allocation_(15,_43) = 1.0
Allocation_(16,_41) = 1.0
Allocation_(17,_41) = 1.0
Allocation_(18,_40) = 1.0
Allocation_(19,_41) = 1.0
Allocation_(2,_42) = 1.0
Allocation_(20,_40) = 1.0
Allocation_(21,_41) = 1.0
Allocation_(22,_43) = 1.0
Allocation_(23,_40) = 1.0
Allocation_(24,_43) = 1.0
Allocation_(25,_41) = 1.0
Allocation_(26,_43) = 1.0
Allocation_(27,_41) = 1.0
Allocation_(28,_43) = 1.0
Allocation_(29,_41) = 1.0
Allocation_(3,_41) = 1.0
Allocation_(30,_41) = 1.0
Allocation_(31,_43) = 1.0
Allocation_(32,_42) = 1.0
Allocation_(33,_41) = 1.0
Allocation_(34,_41) = 1.0
Allocation_(35,_41) = 1.0
Allocation_(36,_43) = 1.0
Allocation_(37,_43) = 1.0
Allocation_(38,_41) = 1.0
Allocation_(39,_42) = 1.0
Allocation_(4,_41) = 1.0
Allocation_(5,_41) = 1.0
Allocation_(6,_43) = 1.0
Allocation_(7,_41) = 1.0
Allocation_(8,_41) =

In [24]:
# Depots and its customers

allot = {}

for i in C:
    for j in D:
        if (a[(i,j)].varValue) > 0:
            if j in allot:
                temp = allot[j]
                temp.append(i)
                allot[j] = temp
            else:
                allot[j] = [i]

print(allot)

{43: [0, 6, 9, 10, 12, 15, 22, 24, 26, 28, 31, 36, 37], 41: [1, 3, 4, 5, 7, 8, 11, 13, 14, 16, 17, 19, 21, 25, 27, 29, 30, 33, 34, 35, 38], 42: [2, 32, 39], 40: [18, 20, 23]}


In [25]:
# Sorting the customers according to latest time within depots

sorted_allot = {}
for depot, customers in allot.items():
    sorted_customers = sorted(customers, key=lambda customer: lat[customer], reverse=False)
    sorted_allot[depot] = sorted_customers

print(sorted_allot)

{43: [6, 9, 36, 28, 24, 22, 31, 37, 15, 12, 0, 10, 26], 41: [8, 4, 38, 5, 33, 17, 25, 19, 1, 29, 34, 13, 21, 3, 27, 30, 11, 35, 7, 16, 14], 42: [32, 2, 39], 40: [18, 23, 20]}


In [26]:
ear.extend([0] * no_of_depots)
lat.extend([0] * no_of_depots)

In [27]:
def check_load(temp):
    load = 0
    
    for i in temp:
        load = load + q[i]
    
    if load > Q:
        return False
    else:
        return True

In [28]:
def check_pickup_delivery(temp):
    load = 0
    
    for i in temp:
        load += p[i] - q[i]
        
        if load > Q:
            return False
    
    return True

In [29]:
def check_traveltime(temp, starttime):
    
    time = starttime
    
    i = 0
    j = 1
    while (j < len(temp)):
        time = max((time + d[temp[i]][temp[j]]), ear[temp[j]]) + s
        if (j != (len(temp) - 1)) and ((time - s) > lat[temp[j]]):
            return [False, time]
        
        i += 1
        j += 1
    
    time -= s
    
    if time > H:
        return [False, time]
    
    else:
        return [True, time]

In [30]:
import pdb

In [31]:
result_dict = {}
time_dict = {}
completed_list = []
for depot, cust_list in sorted_allot.items():
    for i in D_V[depot]:
        for j in W:
            if j == 0:
                starttime = service_at_depot
            else:
                starttime = prev_trip_end_time + service_at_depot
                                
            temp = []
            
            for x in range(len(cust_list)):
                
                if cust_list[x] in completed_list:
                    continue
                
                if len(temp) == 0:
                    temp.extend([depot, cust_list[x], depot])
                else:
                    temp.insert(-1,cust_list[x])
                
                if check_load(temp) == False:
                    temp.pop(-2)
                    continue
                
                if check_pickup_delivery(temp) == False:
                    temp.pop(-2)
                    continue
                    
                ans = check_traveltime(temp, starttime)
                
                if ans[0] == False:
                    temp.pop(-2)
                    continue
                               
                else:                                            
                    prev_trip_end_time = ans[1]                       
                    completed_list.append(cust_list[x])
                    # pdb.set_trace()
                
                
            if len(temp) != 0 and len(temp) != 2:
                result_dict[f"V{i}{j}"] = temp
                time_dict[f"V{i}{j}"] = [starttime, prev_trip_end_time]

In [32]:
print(result_dict)

{'V120': [43, 6, 28, 24, 43], 'V121': [43, 31, 37, 15, 10, 43], 'V130': [43, 9, 22, 12, 43], 'V131': [43, 0, 26, 43], 'V140': [43, 36, 43], 'V40': [41, 8, 5, 33, 19, 41], 'V41': [41, 25, 1, 29, 41], 'V42': [41, 35, 14, 41], 'V50': [41, 4, 17, 34, 13, 41], 'V51': [41, 3, 30, 7, 41], 'V60': [41, 38, 21, 27, 16, 41], 'V61': [41, 11, 41], 'V80': [42, 32, 2, 39, 42], 'V00': [40, 18, 23, 40], 'V01': [40, 20, 40]}


In [33]:
# Define the dictionary

# Create a list of numbers from 0 to 40
all_numbers = list(range(40))

# Iterate through the dictionary values and remove the numbers that are present
for values in result_dict.values():
    all_numbers = [x for x in all_numbers if x not in values]

# Print the missing numbers
print("Missing numbers:", all_numbers)

Missing numbers: []


In [34]:
tot_no_cust = 0

for i, j in result_dict.items():
    tot_no_cust += len(j) - 2
    
print(tot_no_cust)

40


In [35]:
print(time_dict)

{'V120': [5, 148], 'V121': [153, 235], 'V130': [5, 153], 'V131': [158, 202], 'V140': [5, 137], 'V40': [5, 148], 'V41': [153, 202], 'V42': [207, 235], 'V50': [5, 189], 'V51': [194, 237], 'V60': [5, 138], 'V61': [143, 174], 'V80': [5, 106], 'V00': [5, 194], 'V01': [199, 206]}


In [36]:
def calc_obj(result_dict):
    
    tot = 0
    
    for i, j in result_dict.items():
        m = 0
        n = 1
        while (n < len(j)):
            tot += d[j[m]][j[n]]
            m += 1
            n += 1
        
    return tot

In [37]:
final_obj = calc_obj(result_dict)
print(final_obj)
store_obj = final_obj

502


In [38]:
routes = []

for i, j in result_dict.items():
    routes.append(j)

print(routes)

times = []

for i, j in time_dict.items():
    times.append(j)
    
print(times)

[[43, 6, 28, 24, 43], [43, 31, 37, 15, 10, 43], [43, 9, 22, 12, 43], [43, 0, 26, 43], [43, 36, 43], [41, 8, 5, 33, 19, 41], [41, 25, 1, 29, 41], [41, 35, 14, 41], [41, 4, 17, 34, 13, 41], [41, 3, 30, 7, 41], [41, 38, 21, 27, 16, 41], [41, 11, 41], [42, 32, 2, 39, 42], [40, 18, 23, 40], [40, 20, 40]]
[[5, 148], [153, 235], [5, 153], [158, 202], [5, 137], [5, 148], [153, 202], [207, 235], [5, 189], [194, 237], [5, 138], [143, 174], [5, 106], [5, 194], [199, 206]]


In [39]:
def check_feasibility_load(temp):
    load = 0
    
    for i in temp:
        load = load + q[i]
    
    if load > Q:
        print("Load not feasible")
        return False
    else:
        return True

In [40]:
def check_pickup_delivery_feasibility(temp):
    load = 0
    
    for i in temp:
        load += p[i] - q[i]
        
        if load > Q:
            print("Pickup not satisfied since load = {}".format(load))
            return False
    
    return True

In [41]:
def find_obj(routes):
    global final_obj
    tot = 0
    
    for i in routes:
        j = 0
        k = 1
        
        while (k < len(i)):
            tot += d[i[j]][i[k]]
            
            j += 1
            k += 1
            
    if tot < final_obj:
        final_obj = tot
        print("Objective value changed : {}".format(final_obj))
        return True
    
    else:
        print("Objective is not less. Final objective = {}, current objective = {}".format(final_obj, tot))
        return False

In [42]:
def check_feasibility_time(temp, times):
    
    print("route to check for time feasibility = {} and time = {} ".format(temp, times))
    
    curr_time = times[0] + s
    
    i = 0
    j = 1
    
    while (j < (len(temp) - 1)):
        curr_time += d[temp[i]][temp[j]]
        
        if curr_time > lat[temp[j]]:
            print("Time window not satisfied. Current time = {} and latest time = {}".format(curr_time, lat[temp[j]]))
            return False
        
        else:
            curr_time = max(curr_time, ear[temp[j]]) + s
            
        print("Current time at node {} = {}".format(temp[j], curr_time))
            
        j += 1
        i += 1   
        
    return True

In [43]:
import pdb

In [44]:
prev_cnt_routes = len(routes)

# Insert Heuristics

In [45]:
lst_obj_values = []
lst_obj_values.append(final_obj)

for itr in range(5):

    completed_cust = []

    while (len(completed_cust) < no_of_customers):

        i = 0
        while i < len(routes):

            j = 1
            while (j < (len(routes[i])) - 1):
                print("Current routes = {} ".format(routes))

                node_inserted = False

                node = routes[i].pop(j)
                print("Node took to check = {}".format(node))

                if node in completed_cust:
                    print("This node has already been checked")
                    routes[i].insert(j, node)
                    j += 1
                    continue

                for k in range(len(routes)):
                    if i == k:
                        print(k, "Took this route is already considered")
                        continue

                    for l in range(1, len(routes[k])):
                        routes[k].insert(l, node)
                        print("Current check {}".format(routes))

                        if (check_feasibility_load(routes[k])) and (check_feasibility_time(routes[k], times[k])) and (find_obj(routes)) and (check_pickup_delivery_feasibility(routes[k])):
                            node_inserted = True
                            completed_cust.append(node)
                            print("Feasible and hence node {} inserted in route {}".format(node, routes[k]))
                            break

                        else:
                            routes[k].pop(l)
                            print("Not inserted")

                    if node_inserted:
                        break

                #pdb.set_trace()

                if node_inserted:
                    if len(routes[i]) == 2:
                        routes.pop(i)
                    break

                else:
                    completed_cust.append(node)
                    routes[i].insert(j, node)


                print("Check completed for node = {}".format(node))
                print(completed_cust)
                j += 1

            if node_inserted:
                print("******************************************************************************")
                break

            print("Check completed for all nodes of a routes = {}".format(routes[i]))
            i += 1

    print("------------------------------------------------------------------------------------------------")
    print(routes)
    print(final_obj)
    lst_obj_values.append(final_obj)
    print("Initial objective = {}, current = {}".format(store_obj, final_obj))
    print("------------------------------------------------------------------------------------------------")
    #pdb.set_trace()
    
    if (lst_obj_values[-1] == lst_obj_values[-2]):
        break

Current routes = [[43, 6, 28, 24, 43], [43, 31, 37, 15, 10, 43], [43, 9, 22, 12, 43], [43, 0, 26, 43], [43, 36, 43], [41, 8, 5, 33, 19, 41], [41, 25, 1, 29, 41], [41, 35, 14, 41], [41, 4, 17, 34, 13, 41], [41, 3, 30, 7, 41], [41, 38, 21, 27, 16, 41], [41, 11, 41], [42, 32, 2, 39, 42], [40, 18, 23, 40], [40, 20, 40]] 
Node took to check = 6
0 Took this route is already considered
Current check [[43, 28, 24, 43], [43, 6, 31, 37, 15, 10, 43], [43, 9, 22, 12, 43], [43, 0, 26, 43], [43, 36, 43], [41, 8, 5, 33, 19, 41], [41, 25, 1, 29, 41], [41, 35, 14, 41], [41, 4, 17, 34, 13, 41], [41, 3, 30, 7, 41], [41, 38, 21, 27, 16, 41], [41, 11, 41], [42, 32, 2, 39, 42], [40, 18, 23, 40], [40, 20, 40]]
Load not feasible
Not inserted
Current check [[43, 28, 24, 43], [43, 31, 6, 37, 15, 10, 43], [43, 9, 22, 12, 43], [43, 0, 26, 43], [43, 36, 43], [41, 8, 5, 33, 19, 41], [41, 25, 1, 29, 41], [41, 35, 14, 41], [41, 4, 17, 34, 13, 41], [41, 3, 30, 7, 41], [41, 38, 21, 27, 16, 41], [41, 11, 41], [42, 32, 2

Load not feasible
Not inserted
Current check [[43, 6, 28, 31, 43], [43, 37, 43], [43, 9, 24, 26, 22, 43], [43, 0, 15, 43], [43, 36, 10, 12, 43], [41, 8, 5, 33, 41], [41, 1, 29, 41], [41, 35, 14, 41], [41, 4, 17, 34, 13, 41], [41, 3, 30, 7, 41], [41, 38, 21, 27, 16, 41], [41, 19, 11, 41], [42, 32, 25, 2, 39, 42], [40, 18, 23, 40], [40, 20, 40]]
Load not feasible
Not inserted
Current check [[43, 6, 28, 31, 43], [43, 37, 43], [43, 9, 24, 26, 22, 43], [43, 0, 15, 43], [43, 36, 10, 12, 43], [41, 8, 5, 33, 41], [41, 1, 29, 41], [41, 35, 14, 41], [41, 4, 17, 34, 13, 41], [41, 3, 30, 7, 41], [41, 38, 21, 27, 16, 41], [41, 19, 11, 41], [42, 32, 2, 25, 39, 42], [40, 18, 23, 40], [40, 20, 40]]
Load not feasible
Not inserted
Current check [[43, 6, 28, 31, 43], [43, 37, 43], [43, 9, 24, 26, 22, 43], [43, 0, 15, 43], [43, 36, 10, 12, 43], [41, 8, 5, 33, 41], [41, 1, 29, 41], [41, 35, 14, 41], [41, 4, 17, 34, 13, 41], [41, 3, 30, 7, 41], [41, 38, 21, 27, 16, 41], [41, 19, 11, 41], [42, 32, 2, 39, 25,

In [46]:
print("------------------------------------------------------------------------------------------------")
print(routes)
print(final_obj)
print("Initial objective = {}, current = {}".format(store_obj, final_obj))
print("------------------------------------------------------------------------------------------------")
print("Initial routes = {}, current = {}".format(prev_cnt_routes, len(routes)))
print(lst_obj_values)

------------------------------------------------------------------------------------------------
[[43, 6, 28, 31, 43], [43, 37, 43], [43, 9, 24, 26, 22, 43], [43, 0, 15, 11, 43], [43, 36, 10, 12, 43], [41, 8, 5, 33, 34, 41], [41, 25, 41], [41, 35, 14, 41], [41, 4, 7, 17, 13, 41], [41, 3, 30, 41], [41, 39, 38, 27, 16, 41], [41, 19, 29, 1, 41], [42, 32, 21, 2, 42], [40, 18, 23, 40], [40, 20, 40]]
406
Initial objective = 502, current = 406
------------------------------------------------------------------------------------------------
Initial routes = 15, current = 15
[502, 410, 406, 406]


In [47]:
store_obj = final_obj

In [48]:
prev_cnt_routes = len(routes)

# Swap Heuristics

In [49]:
lst_obj_values = []
lst_obj_values.append(final_obj)

for itr in range(5):

    completed_cust = []
    
    
    while (len(completed_cust) < no_of_customers):

        i = 0
        while i < len(routes):

            j = 1
            while (j < (len(routes[i])) - 1):
                
                node_inserted = False
                
                if routes[i][j] in completed_cust:
                    print("This node has already been checked")
                    j += 1
                    continue
                    
                for k in range(len(routes)):
                    if i == k:
                        print(k, "This route is already considered")
                        continue

                    for l in range(1, len(routes[k]) - 1):
                        routes[i][j], routes[k][l] = routes[k][l], routes[i][j]
                        print("Current check {}".format(routes))

                        if (check_feasibility_load(routes[k])) and (check_feasibility_time(routes[k], times[k])) and (find_obj(routes)) and (check_pickup_delivery_feasibility(routes[k])) and (check_feasibility_load(routes[i])) and (check_feasibility_time(routes[i], times[i])) and (check_pickup_delivery_feasibility(routes[i])):
                            node_inserted = True
                            completed_cust.append(routes[i][j])
                            print("Feasible and hence node {} inserted in route {}".format(routes[i][j], routes[i], routes[k]))
                            break

                        else:
                            routes[i][j], routes[k][l] = routes[k][l], routes[i][j]
                            print("Not inserted")

                    if node_inserted:
                        break       

                if node_inserted:
                    break

                else:
                    completed_cust.append(routes[i][j])

                print("Check completed for node = {}".format(routes[i][j]))
                print(completed_cust)
                j += 1

            if node_inserted:
                print("******************************************************************************")
                break

            print("Check completed for all nodes of a routes = {}".format(routes[i]))
            i += 1

    print("------------------------------------------------------------------------------------------------")
    print(routes)
    print(final_obj)
    lst_obj_values.append(final_obj)
    print("Initial objective = {}, current = {}".format(store_obj, final_obj))
    print("------------------------------------------------------------------------------------------------")
    pdb.set_trace()
    
    if (lst_obj_values[-1] == lst_obj_values[-2]):
        break        

0 This route is already considered
Current check [[43, 37, 28, 31, 43], [43, 6, 43], [43, 9, 24, 26, 22, 43], [43, 0, 15, 11, 43], [43, 36, 10, 12, 43], [41, 8, 5, 33, 34, 41], [41, 25, 41], [41, 35, 14, 41], [41, 4, 7, 17, 13, 41], [41, 3, 30, 41], [41, 39, 38, 27, 16, 41], [41, 19, 29, 1, 41], [42, 32, 21, 2, 42], [40, 18, 23, 40], [40, 20, 40]]
route to check for time feasibility = [43, 6, 43] and time = [153, 235] 
Time window not satisfied. Current time = 162 and latest time = 109
Not inserted
Current check [[43, 9, 28, 31, 43], [43, 37, 43], [43, 6, 24, 26, 22, 43], [43, 0, 15, 11, 43], [43, 36, 10, 12, 43], [41, 8, 5, 33, 34, 41], [41, 25, 41], [41, 35, 14, 41], [41, 4, 7, 17, 13, 41], [41, 3, 30, 41], [41, 39, 38, 27, 16, 41], [41, 19, 29, 1, 41], [42, 32, 21, 2, 42], [40, 18, 23, 40], [40, 20, 40]]
Load not feasible
Not inserted
Current check [[43, 24, 28, 31, 43], [43, 37, 43], [43, 9, 6, 26, 22, 43], [43, 0, 15, 11, 43], [43, 36, 10, 12, 43], [41, 8, 5, 33, 34, 41], [41, 25,

ipdb> continue
0 This route is already considered
Current check [[43, 37, 28, 22, 43], [43, 6, 43], [43, 9, 24, 26, 31, 43], [43, 12, 15, 11, 43], [43, 36, 10, 0, 43], [41, 8, 7, 16, 34, 41], [41, 25, 41], [41, 35, 14, 41], [41, 4, 5, 17, 19, 41], [41, 3, 30, 41], [41, 32, 38, 27, 33, 41], [41, 13, 29, 1, 41], [42, 39, 21, 2, 42], [40, 18, 23, 40], [40, 20, 40]]
route to check for time feasibility = [43, 6, 43] and time = [153, 235] 
Time window not satisfied. Current time = 162 and latest time = 109
Not inserted
Current check [[43, 9, 28, 22, 43], [43, 37, 43], [43, 6, 24, 26, 31, 43], [43, 12, 15, 11, 43], [43, 36, 10, 0, 43], [41, 8, 7, 16, 34, 41], [41, 25, 41], [41, 35, 14, 41], [41, 4, 5, 17, 19, 41], [41, 3, 30, 41], [41, 32, 38, 27, 33, 41], [41, 13, 29, 1, 41], [42, 39, 21, 2, 42], [40, 18, 23, 40], [40, 20, 40]]
Load not feasible
Not inserted
Current check [[43, 24, 28, 22, 43], [43, 37, 43], [43, 9, 6, 26, 31, 43], [43, 12, 15, 11, 43], [43, 36, 10, 0, 43], [41, 8, 7, 16, 34

ipdb> continue
0 This route is already considered
Current check [[43, 12, 28, 22, 43], [43, 6, 43], [43, 9, 24, 26, 31, 43], [43, 37, 15, 11, 43], [43, 36, 10, 0, 43], [41, 8, 7, 16, 34, 41], [41, 25, 41], [41, 35, 14, 41], [41, 4, 5, 17, 19, 41], [41, 3, 30, 41], [41, 32, 38, 27, 33, 41], [41, 13, 29, 1, 41], [42, 39, 21, 2, 42], [40, 18, 23, 40], [40, 20, 40]]
route to check for time feasibility = [43, 6, 43] and time = [153, 235] 
Time window not satisfied. Current time = 162 and latest time = 109
Not inserted
Current check [[43, 9, 28, 22, 43], [43, 12, 43], [43, 6, 24, 26, 31, 43], [43, 37, 15, 11, 43], [43, 36, 10, 0, 43], [41, 8, 7, 16, 34, 41], [41, 25, 41], [41, 35, 14, 41], [41, 4, 5, 17, 19, 41], [41, 3, 30, 41], [41, 32, 38, 27, 33, 41], [41, 13, 29, 1, 41], [42, 39, 21, 2, 42], [40, 18, 23, 40], [40, 20, 40]]
Load not feasible
Not inserted
Current check [[43, 24, 28, 22, 43], [43, 12, 43], [43, 9, 6, 26, 31, 43], [43, 37, 15, 11, 43], [43, 36, 10, 0, 43], [41, 8, 7, 16, 34

ipdb> continue


In [50]:
print("------------------------------------------------------------------------------------------------")
print(routes)
print(final_obj)
print("Initial objective = {}, current = {}".format(store_obj, final_obj))
print("------------------------------------------------------------------------------------------------")
print("Initial routes = {}, current = {}".format(prev_cnt_routes, len(routes)))
print(lst_obj_values)

------------------------------------------------------------------------------------------------
[[43, 6, 28, 22, 43], [43, 12, 43], [43, 9, 24, 26, 31, 43], [43, 37, 15, 11, 43], [43, 36, 10, 0, 43], [41, 8, 7, 16, 34, 41], [41, 25, 41], [41, 35, 14, 41], [41, 4, 5, 17, 19, 41], [41, 3, 30, 41], [41, 32, 38, 27, 33, 41], [41, 13, 29, 1, 41], [42, 39, 21, 2, 42], [40, 18, 23, 40], [40, 20, 40]]
346
Initial objective = 406, current = 346
------------------------------------------------------------------------------------------------
Initial routes = 15, current = 15
[406, 354, 346, 346]
